- T : 표적 인덱스
- W : 발사대 인덱스
- M_w : 유도탄 인덱스
- m_w : 발사대 m에 적재된 유도탄 수량
- FN_t = 표적 t에 할당 할 수 있는 유도탄의 개수
- ft_wt = 표적 t에 대한 발사대 w의 최초발사가능 시점
- lt_wt = 표적 t에 대한 발사대 w의 최후발사가능시점
- PK _wt = 발사대 w에서 표적 t에 대한 요격 확률
- theta_wt(m) = 표적 t에 발사대 w의 유도탄 m의 할당 여부, 할당 되면 0, 그렇지 않으면 1의 값을 가짐.
- tau_l_wm : 발사대 w에서 유도탄 m의 발사 시점
- tau_ld_m : 발사대 상의 최소 발사 간격

- T (): 표적 인덱스 (int)
- W : 발사대 인덱스 (int)
- M : 유도탄 인덱스 (int)
- m_w : 발사대 m에 적재된 유도탄 수량 (list : len(m_w) = W, int로 구성)
- FN_T (list, len : T) = 표적 t에 할당 할 수 있는 유도탄의 개수
- ft_wt (ndarray) w*t : 표적 t에 대한 발사대 w의 최초발사가능시점
- lt_wt (ndarray) w*t : 표적 t에 대한 발사대 w의 최후발사가능시점
- PK_wt (ndarray) w*t : 발사대 w에서 표적 t에 대한 요격 확률 
- theta_(m,t,w) (function, input : m(int), t(int), w(int), output : theta_wt (bool) ) : 표적 t에 발사대 w의 유도탄 m의 할당 여부, 할당 되면 0, 그렇지 않으면 1의 값을 가짐.
- tau_l_wm (ndarray) w*m_w : 발사대 w에서 유도탄 m의 발사 시점
- tau_ld_m : 발사대 상의 최소 발사 간격

In [3]:
import numpy as np

W = 5
T = 10

FN_T = [1] * T

M = sum(FN_T)

# 0에서 4 사이의 랜덤한 값으로 구성된 W*T 행렬 생성
ft_wt = np.random.rand(W, T) * 4

# 최소 3초 이상의 간격을 갖도록 설정
min_lt_wt = ft_wt + 3
# 발사가능시점으로부터 최소 3초 이상~ 전체 시간 10초 이내의 간격 행렬 생성
inter_lt_wt = 10 - min_lt_wt

# 3에서 10 사이의 랜덤한 값으로 구성된 W*T 행렬 생성
lt_wt = np.random.rand(W, T) * inter_lt_wt + min_lt_wt

# 최초발사가능 시점과 최후발사가능 시점 사이의 간격이 3초 이상을 갖는지 확인
time_intervals_diff = lt_wt - ft_wt

# 표적 t에 발사대 w를 할당할 때의 보상(요격확률) 행렬 생성
PK_wt = np.random.rand(W, T)

# 0.5 이상의 확률
# PK_wt = 0.5 * np.random.rand(W, T) + 0.5


In [4]:
# Initialize a 3D binary matrix of zeros
theta_wt = np.zeros((W, T, M), dtype=int)

# Randomly choose 5 unique positions in the entire matrix
positions = np.random.choice(W*T*M, 5, replace=False)

# Convert the positions to W, T and M indices
w_indices, t_indices, m_indices = np.unravel_index(positions, (W, T, M))

# Assign 1s at the chosen positions
theta_wt[w_indices, t_indices, m_indices] = 1


In [5]:
def objective_fun_1(theta_wt):
    res = 0
    for t in range(T):
        a = 1
        for w in range(W):
            for m in range(M):
                p = 1 - PK_wt[w,t] * theta_wt[w,t,m]
                a *= p
        res += 1-a
    return res

In [6]:
objective_fun_1(theta_wt)

2.1995653660417416

In [7]:

# 동일 유도탄이 다수의 표적에 중복 할당 X
def constraint2(theta_wt):
    W, T, M = theta_wt.shape
    for m in range(M):
        for w in range(W):
            # If the sum exceeds 1, immediately return False
            if np.sum(theta_wt[w,:,m]) > 1:
                return False
    # If none of the sums exceed 1, return True
    return True

# Now we can check the constraint:
print(constraint2(theta_wt))


True


In [8]:
# constraint3
def constraint3(theta_wt):
    W, T, M = theta_wt.shape
    for t in range(T):
        if np.sum(theta_wt[:,t,:]) > FN_T[t]:
            return False
    return True

print(constraint3(theta_wt))

False


$$
|\tau^l_w(m_i)-\tau^l_w(m_j)| \geq \tau^{ld}_w, \quad \forall w \in W, \quad m_i \neq m_j
$$
$$
\forall m_i,m_j\in M_w,,\theta_{w,t}(m_i)=1,\theta_{w,t}(m_j)=1
$$

In [9]:
def constraint4(theta_wt):
    return True

$$
ft_{w,t} \leq \tau^l_w(m)\leq lt_{w,t}, \forall m \in M_w, \theta_{w,t}(m) = 1
$$

In [10]:
indices = np.where(theta_wt == 1)

In [ ]:
failed_positions = set()

while True:
    # Initialize a 3D binary matrix of zeros
    theta_wt = np.zeros((W, T, M), dtype=int)
    
    available_positions = [pos for pos in range(W*T*M) if frozenset([pos]) not in failed_positions]

    if len(available_positions) < M:
        print("모든 가능한 조합을 시도했습니다.")
        break

    positions = np.random.choice(available_positions, M, replace=False)

    # Convert the positions to W, T and M indices
    w_indices, t_indices, m_indices = np.unravel_index(positions, (W, T, M))

    # Assign 1s at the chosen positions
    theta_wt[w_indices, t_indices, m_indices] = 1

    indices = np.where(theta_wt == 1)

    # Convert the indices to a list of tuples
    indices_list = list(zip(*indices))

    # Sort the indices by the second index (M)
    indices_list.sort(key=lambda x: x[1])

    if constraint2(theta_wt) and constraint3(theta_wt):
        print(f"목표 함수 값 : {objective_fun_1(theta_wt)}")
        # Iterate over each group
        for i, group in enumerate(indices_list):
            print(f"타깃 {group[1]}에 대하여 발사대 {group[0]}가 미사일을 발사합니다. 요격확률 : {PK_wt[group[0], group[1]]:.2f}")
    else:
        print("* : 제한 조건 만족하지 못함")
        failed_positions.add(frozenset(positions))
        continue


* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 

KeyboardInterrupt: 

* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 만족하지 못함
* : 제한 조건 

In [ ]:
def your_procedure(f, V, C):
    # f: function that takes a subset of V and returns a positive real number
    # V: universal set
    # C: set of constraints (each constraint c is a function that takes a subset of V and returns a boolean)
    
    S = set()  # Initialize S to the empty set
    R = set()  # Initialize R to the empty set
    last_f = -1 # Some initial value, it just needs to be worse than any possible value of f(S)
    
    while V != S.union(R) and last_f != f(S):
        last_f = f(S)
        
        # Try to add elements to R
        for c in C:
            for u in V.difference(S.union(R)):
                if not c(S.union({u})):
                    R.add(u)
        
        # Find u' to maximize the quality of S
        delta_f = {u: f(S.union({u})) - f(S) for u in V.difference(S.union(R))}
        u_prime = max(delta_f, key=delta_f.get)
        S.add(u_prime)

    return S
